<br>

# Introdução

In [1]:
import os
import ast
import json
import folium
import requests
import numpy as np
import pandas as pd
import geopandas as gpd

In [2]:
#import shutil
#import urllib.request

In [3]:
#!pip install traquitanas --upgrade

In [4]:
import traquitanas.utils as tt

<br>

## Paths

In [5]:
# Inicialmente faz-se necessário criar uma pasta que receberão os dados do IBGE
data_path = os.path.join('..', 'data')
input_path = os.path.join(data_path, 'input')
output_path = os.path.join(data_path, 'output')

output_path_geo = os.path.join(output_path, 'geo')
output_path_tab = os.path.join(output_path, 'tab')

os.makedirs(data_path, exist_ok=True)
os.makedirs(input_path, exist_ok=True)
os.makedirs(output_path, exist_ok=True)
os.makedirs(output_path_geo, exist_ok=True)
os.makedirs(output_path_tab, exist_ok=True)

<br>

# Dados Espaciais

Com a estrutura de pastas criada, é possivel fazer o download dos arquivos disponiblizados pelo IBGE. Há uma infinidade de dados.

- https://servicodados.ibge.gov.br/api/docs

<br>

## São Paulo

In [6]:
# Define qual o código IBGE do Estado
estado = 35

# Define URL
parameters = {
    'formato': 'application/vnd.geo+json',
    'resolucao': '5',
    'qualidade': '4',
}
url = 'https://servicodados.ibge.gov.br/api/v2/malhas/{}'.format(estado)
r = requests.get(url, params=parameters)
print(r.url)

# Define o nome do arquivo que será salvo as informações do IBGE
geojson_file = os.path.join(input_path, 'sp_ibge.geojson')

# Save
with open(geojson_file, 'wb') as f:
    f.write(r.content)

https://servicodados.ibge.gov.br/api/v2/malhas/35?formato=application%2Fvnd.geo%2Bjson&resolucao=5&qualidade=4


In [7]:
file_encoding = tt.predict_encoding(geojson_file)
file_encoding

'ascii'

In [8]:
gdf = gpd.read_file(
    geojson_file    
)

gdf.rename(
    {'codarea': 'id_ibge'},
    axis=1,
    inplace=True
)

# Transforma Coordenadas
gdf = gdf.to_crs(epsg=4326)

# Salva Arquivo
gdf.to_file(
    os.path.join(output_path_geo, 'sp_igbe.gpkg'),
    layer='Limite Municipal',
    driver='GPKG',
    encoding='utf-8'
)
gdf

/home/michel/Documents/conda/envs/pablocarreira-py39/lib/python3.9/site-packages/geopandas/io/file.py:362: FutureWarning: pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.
  pd.Int64Index,


id_ibge                                           geometry
0    3509106  MULTIPOLYGON (((-51.86000 -21.58070, -51.84270...
1    3511003  MULTIPOLYGON (((-51.41930 -20.68100, -51.42430...
2    3514403  MULTIPOLYGON (((-51.48510 -21.42760, -51.47790...
3    3515301  MULTIPOLYGON (((-51.57090 -22.39880, -51.57320...
4    3515350  MULTIPOLYGON (((-52.44560 -22.60820, -52.49880...
..       ...                                                ...
640  3533205  MULTIPOLYGON (((-51.47550 -21.04970, -51.46160...
641  3539202  MULTIPOLYGON (((-51.43400 -22.20540, -51.41710...
642  3541406  MULTIPOLYGON (((-51.24170 -21.73630, -51.22360...
643  3548302  MULTIPOLYGON (((-51.34290 -21.77450, -51.33050...
644  3552908  MULTIPOLYGON (((-51.21940 -22.35500, -51.21930...

[645 rows x 2 columns]

In [9]:
# Map Object
m = folium.Map()

# Folium Object
folium.GeoJson(geojson_file).add_to(m)

# Fit and Plot map
m.fit_bounds(m.get_bounds())
m

<br>

## São Paulo (Memória)

<br>

Ou ainda, ao invés de baixar o arquivo, é possivel fazer com o que o mapa seja criado com a leitura dos dados diretamente do site do IBGE. Nessa função o *encoding* já foi definido, evitando o problema mencionado acima.

In [10]:
r = requests.get(url, params=parameters)
geojson = json.loads(r.text)

In [11]:
# Map Object
m = folium.Map()

# Folium Object
folium.GeoJson(geojson).add_to(m)

# Fit and Plot map
m.fit_bounds(m.get_bounds())
m

<br>

## Estados

In [12]:
# Define qual o código IBGE do Estado
estado = 'UF'

# Define URL
parameters = {
    'formato': 'application/vnd.geo+json',
    #'resolucao': '5',
    #'qualidade': '4',
}
url = 'https://servicodados.ibge.gov.br/api/v3/malhas/paises/BR?intrarregiao={}'.format(estado)
r = requests.get(url, params=parameters)
print(r.url)

# Define o nome do arquivo que será salvo as informações do IBGE
geojson_file = os.path.join(input_path, 'br_estados_ibge.geojson')

# Save
with open(geojson_file, 'wb') as f:
    f.write(r.content)

https://servicodados.ibge.gov.br/api/v3/malhas/paises/BR?intrarregiao=UF&formato=application%2Fvnd.geo%2Bjson


In [13]:
gdf = gpd.read_file(
    geojson_file    
)

gdf.rename(
    {'codarea': 'id_ibge'},
    axis=1,
    inplace=True
)

# Transforma Coordenadas
gdf = gdf.to_crs(epsg=4326)

# Salva Arquivo
gdf.to_file(
    os.path.join(output_path_geo, 'br_igbe.gpkg'),
    layer='Limite Municipal',
    driver='GPKG',
    encoding='utf-8'
)
gdf.head()

/home/michel/Documents/conda/envs/pablocarreira-py39/lib/python3.9/site-packages/geopandas/io/file.py:362: FutureWarning: pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.
  pd.Int64Index,


id_ibge                                           geometry
0       11  POLYGON ((-62.41770 -13.11890, -62.41400 -13.1...
1       12  POLYGON ((-66.81030 -9.81800, -67.03470 -9.719...
2       13  POLYGON ((-58.14740 -7.34320, -58.15430 -7.332...
3       14  POLYGON ((-64.18440 3.48930, -64.16130 3.46500...
4       15  MULTIPOLYGON (((-48.19460 -4.91100, -48.05840 ...
5       16  MULTIPOLYGON (((-50.45010 2.10920, -50.45740 2...
6       17  POLYGON ((-47.43030 -6.42260, -47.41990 -6.401...
7       21  MULTIPOLYGON (((-48.02540 -4.77830, -48.05840 ...
8       22  POLYGON ((-40.76430 -8.24400, -40.74450 -8.240...
9       23  POLYGON ((-40.37190 -2.81240, -40.39160 -2.813...
10      24  POLYGON ((-36.50440 -6.38650, -36.50020 -6.370...
11      25  MULTIPOLYGON (((-37.57180 -7.48910, -37.55690 ...
12      26  MULTIPOLYGON (((-40.95900 -8.84200, -40.94640 ...
13      27  POLYGON ((-38.01210 -9.15600, -38.02580 -9.155...
14      28  POLYGON ((-36.91800 -10.12470, -36.92530 -10.1...
15      29  POLYGON ((-39.35680 -8.54750, -39.36450 -8.537...
16      31  POLYGON ((-47.67970 -18.35610, -47.69400 -18.3...
17      32  MULTIPOLYGON (((-41.27140 -19.94220, -41.29040...
18      33  MULTIPOLYGON (((-44.23150 -23.07530, -44.23680...
19      35  MULTIPOLYGON (((-46.69070 -21.83760, -46.68550...
20      41  POLYGON ((-48.91230 -24.67400, -48.93100 -24.6...
21      42  MULTIPOLYGON (((-52.15880 -26.46620, -52.16670...
22      43  MULTIPOLYGON (((-53.94750 -31.95460, -53.93230...
23      50  POLYGON ((-53.40390 -17.99260, -53.41790 -17.9...
24      51  POLYGON ((-56.27230 -9.40080, -56.67190 -9.367...
25      52  POLYGON ((-48.23490 -15.66000, -48.23420 -15.6...
26      53  POLYGON ((-47.31000 -16.03630, -47.31690 -16.0...

In [14]:
# API
list_estados = []
for index, row in gdf.iterrows():
    url = 'https://servicodados.ibge.gov.br/api/v1/localidades/estados/{UF}'.format(UF=row['id_ibge'])
    r = requests.get(url)
    dict_quotes = r.content.decode(r.encoding)
    dict_quotes = ast.literal_eval(dict_quotes)
    list_estados.append(dict_quotes)
    
# Transforma dictionary in Dataframe
df = pd.DataFrame(list_estados)
df.head()

# Adjust nested Dictionary
for i, row in df.iterrows():
    df.loc[i, 'id_regiao'] = row['regiao']['id']
    df.loc[i, 'sigla_regiao'] = row['regiao']['sigla']
    df.loc[i, 'nome_regiao'] = row['regiao']['nome']

# Fim
df.drop(['regiao'], axis=1, inplace=True)
df['id_regiao'] = pd.to_numeric(df['id_regiao'], downcast='integer')
df.head()

id sigla                 nome  id_regiao sigla_regiao   nome_regiao
0   11    RO             Rondônia          1            N         Norte
1   12    AC                 Acre          1            N         Norte
2   13    AM             Amazonas          1            N         Norte
3   14    RR              Roraima          1            N         Norte
4   15    PA                 Pará          1            N         Norte
5   16    AP                Amapá          1            N         Norte
6   17    TO            Tocantins          1            N         Norte
7   21    MA             Maranhão          2           NE      Nordeste
8   22    PI                Piauí          2           NE      Nordeste
9   23    CE                Ceará          2           NE      Nordeste
10  24    RN  Rio Grande do Norte          2           NE      Nordeste
11  25    PB              Paraíba          2           NE      Nordeste
12  26    PE           Pernambuco          2           NE      Nordeste
13  27    AL              Alagoas          2           NE      Nordeste
14  28    SE              Sergipe          2           NE      Nordeste
15  29    BA                Bahia          2           NE      Nordeste
16  31    MG         Minas Gerais          3           SE       Sudeste
17  32    ES       Espírito Santo          3           SE       Sudeste
18  33    RJ       Rio de Janeiro          3           SE       Sudeste
19  35    SP            São Paulo          3           SE       Sudeste
20  41    PR               Paraná          4            S           Sul
21  42    SC       Santa Catarina          4            S           Sul
22  43    RS    Rio Grande do Sul          4            S           Sul
23  50    MS   Mato Grosso do Sul          5           CO  Centro-Oeste
24  51    MT          Mato Grosso          5           CO  Centro-Oeste
25  52    GO                Goiás          5           CO  Centro-Oeste
26  53    DF     Distrito Federal          5           CO  Centro-Oeste

In [15]:
df.to_csv(
    os.path.join(output_path_tab, 'tab_ufs_ibge.csv'),
    index=False
)

In [16]:
# Map Object
m = folium.Map()

# Folium Object
folium.GeoJson(geojson_file).add_to(m)

# Fit and Plot map
m.fit_bounds(m.get_bounds())
m

<br>

Uma vez com o mapa na mão, de qualquer que seja o meio que foi obtido, é possivel analisar a "tabela de atributos".
Lá descobrimos que existe o par de coordenadas que define o centroide e, ainda, o 'codarea' que tem o código do IBGE do município.

<br>

# Dados Tabulares

In [17]:
df_ufs = pd.read_csv(
    os.path.join(output_path_tab, 'tab_ufs_ibge.csv'),
)

list_dfs = []
for i, row  in df_ufs.iterrows():
    estado = row['id']
    url = 'http://servicodados.ibge.gov.br/api/v1/localidades/estados/{}/municipios'.format(estado)    
    df = pd.read_json(url)
    list_dfs.append(df)

# Ajustes
df = pd.concat(list_dfs)
df = df[['id', 'nome']].copy()

# Salva
df.to_csv(
    os.path.join(output_path_tab, 'tab_municipios_ibge.csv'),
    index=False
)
df.head()

id                   nome
0  1100015  Alta Floresta D'Oeste
1  1100023              Ariquemes
2  1100031                 Cabixi
3  1100049                 Cacoal
4  1100056             Cerejeiras

In [18]:
# Defines IBGE Code State
estado = 35

# Defines URL
url = 'http://servicodados.ibge.gov.br/api/v1/localidades/estados/{}/municipios'.format(estado)
print('{}\n'.format(url))

# Create Dataframe
df = pd.read_json(url)

# Seleciona Colunas
df = df[['id', 'nome']]

# Renomeia Colunas
df = df.rename(columns=lambda x: x.replace('id', 'id_ibge'))
df

http://servicodados.ibge.gov.br/api/v1/localidades/estados/35/municipios



id_ibge              nome
0    3500105        Adamantina
1    3500204            Adolfo
2    3500303             Aguaí
3    3500402    Águas da Prata
4    3500501  Águas de Lindóia
..       ...               ...
640  3557006        Votorantim
641  3557105       Votuporanga
642  3557154          Zacarias
643  3557204         Chavantes
644  3557303      Estiva Gerbi

[645 rows x 2 columns]

<br>

# Mapa Categórico

In [19]:
# Adjust dtypes
#df['id_ibge'] = df['id_ibge'].apply(lambda x: str(x))

# Add Random Colum
df['random'] = np.random.uniform(1, 6, df.shape[0])

# Results
print('{}\n'.format(df.dtypes))
display(df.head())

id_ibge      int64
nome        object
random     float64
dtype: object



id_ibge              nome    random
0  3500105        Adamantina  3.085110
1  3500204            Adolfo  1.104913
2  3500303             Aguaí  3.643677
3  3500402    Águas da Prata  5.980800
4  3500501  Águas de Lindóia  1.249895

In [24]:
# Geodataframe
gdf = gpd.read_file(
    os.path.join(output_path_geo, 'sp_igbe.gpkg')
)

# Ajusta os Tipo
gdf['id_ibge'] = pd.to_numeric(gdf['id_ibge'], downcast='integer')

# Results
print('{}\n'.format(gdf.dtypes))
display(gdf.head())

id_ibge        int32
geometry    geometry
dtype: object



id_ibge                                           geometry
0  3509106  MULTIPOLYGON (((-51.86000 -21.58070, -51.84270...
1  3511003  MULTIPOLYGON (((-51.41930 -20.68100, -51.42430...
2  3514403  MULTIPOLYGON (((-51.48510 -21.42760, -51.47790...
3  3515301  MULTIPOLYGON (((-51.57090 -22.39880, -51.57320...
4  3515350  MULTIPOLYGON (((-52.44560 -22.60820, -52.49880...

In [25]:
# Create Map
m = folium.Map()

highlight_function = lambda x: {
    'fillColor': '#000000', 
    'color':'#000000',
    'fillOpacity': 30,
    'weight': 1
}

choropleth = folium.Choropleth(
    geo_data=gdf,
    name='choropleth',    
    data=df,
    columns=['id_ibge', 'random', 'nome'],
    key_on='feature.properties.id_ibge',
    fill_color='YlGnBu',
    fill_opacity=0.5,
    line_opacity=0.1,
    legend_name='Legenda',
    smooth_factor=0,
    show=False,
    overlay=True,
    highlight=True,
    highlight_function=highlight_function,
    nan_fill_color='White',
).add_to(m)

# Add Field in geodataframe
choropleth.geojson.add_child(
    folium.features.GeoJsonTooltip(['id_ibge'], labels=False)
)

# Fit and Plot map
m.fit_bounds(m.get_bounds())
m